In [50]:
import pandas as pd
import altair as alt
from collections import Counter

In [51]:
df = pd.read_csv('application_data_min.csv')
df.loc[df['CNT_FAM_MEMBERS'].isnull()] = 0
df = df.dropna(subset = ['AMT_ANNUITY'])

X = df[['CNT_FAM_MEMBERS', 'AMT_INCOME_TOTAL', 'AMT_CREDIT', 'AMT_ANNUITY', 'CODE_GENDER', 'NAME_CONTRACT_TYPE', 
       'NAME_EDUCATION_TYPE']]
X = pd.get_dummies(X, drop_first = True)

y = df['TARGET']

In [52]:
X.describe()

CNT_FAM_MEMBERS  AMT_INCOME_TOTAL    AMT_CREDIT    AMT_ANNUITY  \
count    307499.000000      3.074990e+05  3.074990e+05  307499.000000   
mean          2.152667      1.687951e+05  5.990232e+05   27108.369030   
std           0.910705      2.371272e+05  4.024955e+05   14493.896738   
min           0.000000      0.000000e+00  0.000000e+00       0.000000   
25%           2.000000      1.125000e+05  2.700000e+05   16524.000000   
50%           2.000000      1.468125e+05  5.135310e+05   24903.000000   
75%           3.000000      2.025000e+05  8.086500e+05   34596.000000   
max          20.000000      1.170000e+08  4.050000e+06  258025.500000   

       CODE_GENDER_F  CODE_GENDER_M  CODE_GENDER_XNA  \
count  307499.000000   307499.00000    307499.000000   
mean        0.658340        0.34164         0.000013   
std         0.474267        0.47426         0.003607   
min         0.000000        0.00000         0.000000   
25%         0.000000        0.00000         0.000000   
50%         1.000000        0.00000         0.000000   
75%         1.000000        1.00000         0.000000   
max         1.000000        1.00000         1.000000   

       NAME_CONTRACT_TYPE_Cash loans  NAME_CONTRACT_TYPE_Revolving loans  \
count                  307499.000000                       307499.000000   
mean                        0.904783                            0.095210   
std                         0.293514                            0.293505   
min                         0.000000                            0.000000   
25%                         1.000000                            0.000000   
50%                         1.000000                            0.000000   
75%                         1.000000                            0.000000   
max                         1.000000                            1.000000   

       NAME_EDUCATION_TYPE_Academic degree  \
count                        307499.000000   
mean                              0.000533   
std                               0.023088   
min                               0.000000   
25%                               0.000000   
50%                               0.000000   
75%                               0.000000   
max                               1.000000   

       NAME_EDUCATION_TYPE_Higher education  \
count                         307499.000000   
mean                               0.243438   
std                                0.429158   
min                                0.000000   
25%                                0.000000   
50%                                0.000000   
75%                                0.000000   
max                                1.000000   

       NAME_EDUCATION_TYPE_Incomplete higher  \
count                          307499.000000   
mean                                0.033418   
std                                 0.179726   
min                                 0.000000   
25%                                 0.000000   
50%                                 0.000000   
75%                                 0.000000   
max                                 1.000000   

       NAME_EDUCATION_TYPE_Lower secondary  \
count                        307499.000000   
mean                              0.012403   
std                               0.110677   
min                               0.000000   
25%                               0.000000   
50%                               0.000000   
75%                               0.000000   
max                               1.000000   

       NAME_EDUCATION_TYPE_Secondary / secondary special  
count                                      307499.000000  
mean                                            0.710201  
std                                             0.453670  
min                                             0.000000  
25%                                             0.000000  
50%                                             1.000000  
75%                                             1.000000  


In [53]:
y.value_counts() / len(y)

0    0.919268
1    0.080732
Name: TARGET, dtype: float64

In [54]:
y.value_counts()

0    282674
1     24825
Name: TARGET, dtype: int64

In [55]:
y_values = pd.DataFrame({'values':['0', '1'], 'count':[y.value_counts()[0], y.value_counts()[1]]})

In [56]:
alt.Chart(y_values).mark_bar().encode(
    x = 'values',
    y = 'count'
)

alt.Chart(...)

Note that we had to hardcode these values because of 

## Option 1: Random Sampling

In [57]:
defaults = df[df['TARGET'] == 1]
nondefaults = df[df['TARGET'] == 0]

In [58]:
num_defaults = int(5000 * 0.080732)
num_nondefaults = 5000 - num_defaults

In [59]:
default_sample = defaults.sample(n = num_defaults)
nondefault_sample = nondefaults.sample(n = num_nondefaults)
sample = pd.concat([default_sample, nondefault_sample])

In [60]:
print(sample['TARGET'].value_counts())

0    4597
1     403
Name: TARGET, dtype: int64


In [67]:
alt.Chart(sample).mark_bar().encode(
    x = 'TARGET:O',
    y = 'count()'
)

alt.Chart(...)

In [70]:
brush = alt.selection_interval(encodings=['x'])

base = alt.Chart(sample).mark_bar().encode(
    y='count():Q'
).properties(
    width=600,
    height=100
)

alt.vconcat(
  base.encode(
    alt.X('AMT_INCOME_TOTAL:Q',
      bin=alt.Bin(maxbins=30, extent=brush),
      scale=alt.Scale(domain=brush)
    )
  ),
  base.encode(
    alt.X('AMT_INCOME_TOTAL:Q', bin=alt.Bin(maxbins=100)),
  ).add_selection(brush)
)

alt.VConcatChart(...)

In [73]:
alt.Chart(sample).mark_rect().encode(
    alt.X("AMT_CREDIT:Q", bin=True),
    alt.Y("AMT_ANNUITY:Q", bin=True),
    color='count()'
)

alt.Chart(...)

In [75]:
alt.Chart(sample).mark_rect().encode(
    alt.X("AMT_CREDIT:Q", bin=True),
    alt.Y("AMT_INCOME_TOTAL:Q", bin=True),
    color='count()'
)

alt.Chart(...)

## Option 2: Discretize into Bins

In [62]:
df['FAMILY_BIN'] = pd.cut(df['CNT_FAM_MEMBERS'], bins = [0, 5, 10, 15, 20])
df['FAMILY_BIN'].value_counts()

(0, 5]      306968
(5, 10]        518
(10, 15]         7
(15, 20]         4
Name: FAMILY_BIN, dtype: int64

In [63]:
# Splits into 10 bins
df['INCOME_BIN'] = pd.qcut(df['AMT_INCOME_TOTAL'], q=10)
df['INCOME_BIN'].value_counts().reindex(df['INCOME_BIN'].cat.categories)

(-0.001, 81000.0]          33393
(81000.0, 99000.0]         30278
(99000.0, 112500.0]        36907
(112500.0, 135000.0]       48849
(135000.0, 146812.5]        4324
(146812.5, 162000.0]       31126
(162000.0, 180000.0]       30702
(180000.0, 225000.0]       44805
(225000.0, 270000.0]       19957
(270000.0, 117000000.0]    27158
Name: INCOME_BIN, dtype: int64

Note: not really sure how to plot these, altair doesn't seem to like the fact that they're intervals